#Preparando análises

##Separando em 4 quadrantes os oceanos que envolvem a américa do sul

In [ ]:
max_lat = 6
min_lat = -34
max_lon = -3.9
min_lon = -180
fronteira_lat = -20
fronteira_lon = -37.5

quadrante_mar_lat_lon = {
    'mar_nordeste': {
            'lat':(fronteira_lat,max_lat),
            'lon':(fronteira_lon,max_lon)
    },
    'mar_suldeste': {
            'lat':(min_lat,fronteira_lat),
            'lon':(fronteira_lon,max_lon)
    },
    'mar_noroeste': {
            'lat':(fronteira_lat,max_lat),
            'lon':(min_lon,fronteira_lon)
    },
    'mar_sudoeste': {
            'lat':(min_lat,fronteira_lat),
            'lon':(min_lon,fronteira_lon)
    }
}

In [ ]:
bronze_surftemp = '/mnt/usp/ProjetoIntegrador/bronze/surftemp-sst'
mar_temp_df = spark.read.format("parquet").load(bronze_surftemp)

In [ ]:
import pyspark.sql.functions as F
import pyspark.sql.types as StringType

def get_mar_quadrante(lat, lon):
    for quadrante, ranges in quadrante_mar_lat_lon.items():
        lat_range, lon_range = ranges['lat'], ranges['lon']
        if lat_range[0] <= lat < lat_range[1] and lon_range[0] <= lon < lon_range[1]:
            return quadrante
    return 'demais'

get_mar_quadrante_udf = F.udf(get_mar_quadrante)

mar_quadrante_temp_df = (
    mar_temp_df
    .withColumn("quadrante_mar", get_mar_quadrante_udf(F.col("lat"), F.col("lon")))
    .groupBy("time","year","month","day")
    .pivot("quadrante_mar")
    .agg((F.avg("analysed_sst") - F.lit(273.15)).alias("temp_mar_quadrante"))
    .drop("demais")
)

In [ ]:
mar_quadrante_temp_df.display()

time year month day mar_nordeste mar_noroeste mar_sudoeste mar_suldeste 2020-11-11 2020 11 11 298.92181912493504 298.12667100331316 293.88995257616494 294.00565618252267 2020-05-21 2020 5 21 300.8735381410489 300.305446251077 295.4228122929547 295.904345690312 2020-12-20 2020 12 20 299.12926503921005 298.4016230238594 295.6677429668224 296.8161030998035 2020-08-21 2020 8 21 298.0385594556565 298.16985515615045 292.8027449905719 293.3270638032835 2020-02-04 2020 2 4 301.26185904617637 300.08699331907 297.397837112816 298.29579140215503 2020-07-22 2020 7 22 298.78711100124576 298.78926009801273 293.2606779079258 293.747055127345 2020-02-01 2020 2 1 301.13271626032406 300.1204575227241 297.3347540584254 298.3962482984374 2020-09-04 2020 9 4 298.0847201324066 297.8746537965853 292.7940701860714 293.1753499709019 2020-11-18 2020 11 18 298.99621964461966 298.14811858115235 294.32597306031624 294.2251174584538 2020-10-31 2020 10 31 298.7929987969285 297.8198516193767 293.5145393084308 293.5551729272012 2020-07-01 2020 7 1 299.3517620022191 299.27592989884437 293.8152845550784 294.30635221507276 2020-11-30 2020 11 30 298.954421407977 298.2001105901049 294.94633013037094 295.28887649377185 2020-09-10 2020 9 10 298.0955614536624 297.82015690831815 292.7886664186607 293.0881291592202 2020-01-12 2020 1 12 300.7008965814065 299.6517126978668 296.6171428098226 298.10438021072724 2020-11-16 2020 11 16 298.9644990211681 298.18561990762373 294.22727479974577 294.0426687466044 2020-05-26 2020 5 26 300.70939905043633 300.13538408013835 295.1073764874316 295.68862062522345 2020-08-07 2020 8 7 298.3815291691355 298.33517746999695 293.0272471348926 293.38292889724784 2020-05-22 2020 5 22 300.8265060779243 300.27285360505067 295.3390755426131 295.83721641180466 2020-01-24 2020 1 24 300.92005145311583 299.87021100868964 297.21594507705987 298.0367142459973 2020-04-04 2020 4 4 301.73940163421787 300.9865692922232 297.0246949030924 297.86403523594345 2020-07-09 2020 7 9 299.05970843499125 299.0658703876736 293.53935247432827 294.10611957368394 2020-07-14 2020 7 14 298.92742604825037 298.9120212737193 293.3951921189742 293.92468715703404 2020-03-03 2020 3 3 301.6273463944062 300.5547926558345 297.57525974130317 298.3606523564073 2020-09-18 2020 9 18 298.07179020683344 297.78237354076975 292.8364418589497 293.11469125115144 2020-01-13 2020 1 13 300.7273186029349 299.64871171168954 296.6597020325821 298.0308723949251 2020-05-29 2020 5 29 300.63660818680717 300.12870246236923 295.0210149643917 295.62015907034584 2020-07-25 2020 7 25 298.66592142507363 298.6901251017546 293.1898255245351 293.6211786625337 2020-04-01 2020 4 1 301.7793882776372 300.9560725427639 297.1611651998913 298.0600686582578 2020-01-27 2020 1 27 300.89026505314007 300.0121049705938 297.3001107392084 298.0387459216475 2020-10-20 2020 10 20 298.73135616337345 297.8657582899152 293.3203116882564 293.5293997954349 2020-04-12 2020 4 12 301.73968054934005 301.0972611797172 296.8567702626508 297.7462596546225 2020-06-27 2020 6 27 299.45785588910843 299.38436219095775 293.9544203132342 294.36558385706275 2020-06-30 2020 6 30 299.37555309356804 299.3222605566442 293.8509616942992 294.3419592039926 2020-10-08 2020 10 8 298.5390128348134 297.78650674319334 292.96053995357806 293.27152085109634 2020-05-05 2020 5 5 301.35499386293264 300.6350622832148 296.0375312227387 296.7699825893454 2020-08-26 2020 8 26 298.1702443216845 298.14584600383535 292.83484132948854 293.2322544824509 2020-10-16 2020 10 16 298.716715632537 297.82071242249367 293.0915261478325 293.29764913085364 2020-08-29 2020 8 29 298.1219665718961 298.0553816345394 292.82502662399355 293.25560793471175 2020-08-19 2020 8 19 298.00841556207416 298.22976508960056 292.84492418727774 293.32094961283155 2020-08-15 2020 8 15 298.0905883166173 298.3087894799262 292.8939353004723 293.30389454689157 2020-08-14 2020 8 14 298.1271008651371 298.31979015578736 292.90833187035366 293.2895905060022 2020-08-18 2020 8 18 298.01322857592385 298.277521095

##Adicionando dados de temperatura por dia por cidade

In [ ]:
bronze_climatico = '/mnt/usp/ProjetoIntegrador/bronze/climaticos/'
ibge_cidade_codigo = "/mnt/historyzoneprod/Brazil/Manual/Sales/DigitalInsights/RevenueManagement/DataAcquisition/Ibm/LatLonCad"

In [ ]:
def snake_case(s):
    from re import sub
    from unidecode import unidecode
    return sub('[^a-z0-9_]', '', unidecode('_'.join(
        sub('([A-Z][a-z]+)', r' \1',
        sub('([A-Z]+)', r' \1',
        s.replace('-',' '))).split()).lower())).replace('__','_')
    
snake_case_udf = F.udf(snake_case)

In [ ]:
climatico_df = (
    spark.read.format("parquet").load(bronze_climatico)
    .select("latitude","longitude","precip24Hour","relativeHumidity","temperature","year","month","day","codigo")
    .join(spark.read.format("parquet").load(ibge_cidade_codigo).select("codigo","municipio","nome_uf"), "codigo")
    .withColumn("municipio",snake_case_udf("municipio"))
    .withColumn("nome_uf",snake_case_udf("nome_uf"))
)

In [ ]:
climatico_df.display()

codigo latitude longitude precip24Hour relativeHumidity temperature year month day municipio nome_uf 1200203 -7.626373626373635 -72.6855652660139 2.7 93.7 24.4 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 2.4 95.6 23.6 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 2.2 96.5 23.0 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 1.8 97.0 22.9 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 1.3 98.5 22.4 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.8 98.0 22.5 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.6 98.0 21.9 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.3 98.5 21.9 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.1 100.0 21.6 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.1 100.0 21.4 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.1 100.0 21.1 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.1 99.0 21.4 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 96.5 22.2 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 91.3 24.0 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 81.4 25.9 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 72.9 27.8 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 69.0 28.7 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 65.0 29.5 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 62.8 30.1 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 60.3 30.7 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 61.2 30.3 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 66.3 29.5 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 74.4 27.6 2023 2 21 cruzeiro_do_sul acre 1200203 -7.626373626373635 -72.6855652660139 0.0 83.1 25.8 2023 2 21 cruzeiro_do_sul acre 1200328 -9.42857142857143 -71.8945497765742 0.6 79.4 23.9 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.6 82.2 23.3 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.6 84.7 22.8 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.6 86.5 22.5 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.7 89.1 22.4 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.8 90.0 22.2 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.8 91.8 21.6 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.8 92.3 21.4 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.8 93.2 21.2 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.5 94.1 20.9 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.2 94.6 20.7 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 93.2 21.1 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 88.2 22.6 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 78.6 24.6 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 69.7 26.5 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 62.8 28.1 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 57.6 29.3 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 54.6 30.2 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 51.4 31.0 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 49.9 31.3 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 54.0 30.4 2023 2 21 jordao acre 1200328 -9.42857142857143 -71.8945497765742 0.0 57.6 29.

##Dados de produção e valor da produção por cidade

In [ ]:
bronze_pam = '/mnt/usp/ProjetoIntegrador/bronze/pam/'
pam_df = spark.read.format("parquet").load(bronze_pam)

In [ ]:
from pyspark.sql.window import Window

pam_df = (
    pam_df
    .select(F.col("regiao").alias("municipio"),"area_colhida_hectares","valor_da_producao_mil_reais","tipo_lavoura","year","file_path")
    .join(
        pam_df
        .withColumn("marcador_estado", F.row_number().over(Window.partitionBy("file_path").orderBy(F.col("area_colhida_hectares").desc())))
        .filter(F.col("marcador_estado") == 1)
        .select("file_path",F.col("regiao").alias("nome_uf")),
        "file_path"
    )
    .drop("file_path")
    .withColumn("municipio",snake_case_udf("municipio"))
    .withColumn("nome_uf",snake_case_udf("nome_uf"))
)

In [ ]:
pam_df.display()

municipio area_colhida_hectares valor_da_producao_mil_reais tipo_lavoura year nome_uf fonte_ibge_producao_agricola_municipal null null lavouras_permanentes 2020 maranhao sao_raimundo_das_mangabeiras 188.0 800.0 lavouras_permanentes 2020 maranhao sao_felix_de_balsas null null lavouras_permanentes 2020 maranhao sao_domingos_do_azeitao 9.0 91.0 lavouras_permanentes 2020 maranhao sambaiba 15.0 144.0 lavouras_permanentes 2020 maranhao nova_colinas 23.0 101.0 lavouras_permanentes 2020 maranhao loreto 16.0 150.0 lavouras_permanentes 2020 maranhao fortaleza_dos_nogueiras 17.0 48.0 lavouras_permanentes 2020 maranhao benedito_leite 6.0 67.0 lavouras_permanentes 2020 maranhao chapadas_das_mangabeiras 274.0 1400.0 lavouras_permanentes 2020 maranhao tasso_fragoso null null lavouras_permanentes 2020 maranhao riachao 36.0 342.0 lavouras_permanentes 2020 maranhao feira_nova_do_maranhao null null lavouras_permanentes 2020 maranhao balsas 172.0 1593.0 lavouras_permanentes 2020 maranhao alto_parnaiba 9.0 49.0 lavouras_permanentes 2020 maranhao gerais_de_balsas 217.0 1984.0 lavouras_permanentes 2020 maranhao sao_pedro_dos_crentes 2.0 13.0 lavouras_permanentes 2020 maranhao sao_joao_do_paraiso 312.0 4555.0 lavouras_permanentes 2020 maranhao porto_franco 157.0 2627.0 lavouras_permanentes 2020 maranhao estreito 2.0 3.0 lavouras_permanentes 2020 maranhao carolina 70.0 877.0 lavouras_permanentes 2020 maranhao campestre_do_maranhao 35.0 468.0 lavouras_permanentes 2020 maranhao porto_franco 578.0 8542.0 lavouras_permanentes 2020 maranhao sul_maranhense 1069.0 11925.0 lavouras_permanentes 2020 maranhao sucupira_do_riachao 10.0 98.0 lavouras_permanentes 2020 maranhao sucupira_do_norte 12.0 127.0 lavouras_permanentes 2020 maranhao sao_joao_dos_patos 41.0 407.0 lavouras_permanentes 2020 maranhao sao_francisco_do_maranhao 21.0 33.0 lavouras_permanentes 2020 maranhao pastos_bons 18.0 160.0 lavouras_permanentes 2020 maranhao passagem_franca 107.0 111.0 lavouras_permanentes 2020 maranhao paraibano 10.0 101.0 lavouras_permanentes 2020 maranhao nova_iorque 22.0 343.0 lavouras_permanentes 2020 maranhao mirador 42.0 170.0 lavouras_permanentes 2020 maranhao lagoa_do_mato 9.0 44.0 lavouras_permanentes 2020 maranhao jatoba 14.0 20.0 lavouras_permanentes 2020 maranhao colinas 140.0 85.0 lavouras_permanentes 2020 maranhao barao_de_grajau 107.0 126.0 lavouras_permanentes 2020 maranhao chapadas_do_alto_itapecuru 553.0 1822.0 lavouras_permanentes 2020 maranhao timon 731.0 1440.0 lavouras_permanentes 2020 maranhao sao_joao_do_soter 6.0 12.0 lavouras_permanentes 2020 maranhao parnarama 33.0 20.0 lavouras_permanentes 2020 maranhao matoes 223.0 68.0 lavouras_permanentes 2020 maranhao caxias 32.0 43.0 lavouras_permanentes 2020 maranhao buriti_bravo 54.0 63.0 lavouras_permanentes 2020 maranhao caxias 1079.0 1645.0 lavouras_permanentes 2020 maranhao duque_bacelar 5.0 9.0 lavouras_permanentes 2020 maranhao coelho_neto 8.0 14.0 lavouras_permanentes 2020 maranhao aldeias_altas 5.0 17.0 lavouras_permanentes 2020 maranhao afonso_cunha 4.0 7.0 lavouras_permanentes 2020 maranhao coelho_neto 22.0 49.0 lavouras_permanentes 2020 maranhao timbiras 9.0 20.0 lavouras_permanentes 2020 maranhao peritoro 8.0 15.0 lavouras_permanentes 2020 maranhao coroata 11.0 21.0 lavouras_permanentes 2020 maranhao codo 21.0 36.0 lavouras_permanentes 2020 maranhao capinzal_do_norte 7.0 73.0 lavouras_permanentes 2020 maranhao alto_alegre_do_maranhao 3.0 6.0 lavouras_permanentes 2020 maranhao codo 59.0 173.0 lavouras_permanentes 2020 maranhao urbano_santos 89.0 159.0 lavouras_permanentes 2020 maranhao sao_benedito_do_rio_preto 16.0 41.0 lavouras_permanentes 2020 maranhao milagres_do_maranhao 59.0 108.0 lavouras_permanentes 2020 maranhao mata_roma 62.0 111.0 lavouras_permanentes 2020 maranhao chapadinha 77.0 95.0 lavouras_permanentes 2020 maranhao buriti 73.0 91.0 lavouras_permanentes 2020 maranhao brejo 100.0 82.0 lavouras_permanentes 2020 maranhao belagua 33.0 59.0 lavouras_permanentes 2020 maranhao anapurus 120

In [ ]:
df = (
    climatico_df
    .join(pam_df, ['municipio','nome_uf','year'])
    .join(mar_quadrante_temp_df, ["year","month","day"])
)

In [ ]:
df.display()

In [ ]:
silver = '/mnt/usp/ProjetoIntegrador/silver/features/'
df.write.format("parquet").mode("overwrite").save(silver)